# Kelly Criterion

## Initial Example

In [102]:
# Import libraries
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import yfinance as yf

np.random.seed(25)
pd.set_option('display.float_format', lambda x: '%.2f' % x)

In [103]:
# Create function of random win-lose bets
def random_bets(bets, winning_probability):
    outputs = np.random.choice(a=[-1, 1], p=[1-winning_probability, winning_probability], size=bets)
    return outputs

In [104]:
# Create function of cumulative results from bets
def cumulative_bets(initial_amount, bet_size_list, bets, winning_probability):
    outputs = random_bets(bets=bets, winning_probability=winning_probability)
    results_df = pd.DataFrame()
    
    for bet_size in bet_size_list:

        amount = initial_amount
        results = []
        results.append(amount)
        
        for output in outputs:
            amount = amount + amount*bet_size*output
            results.append(amount)

        results_df[bet_size] = results

    return outputs, results_df

In [105]:
# Define parameters
initial_amount = 1
bet_size_list = [0.01, 0.02, 0.04, 0.08, 0.15, 0.20]
bets = 1000
winning_probability = 0.52

# Run functions and plot results
outputs, df = cumulative_bets(initial_amount=initial_amount, bet_size_list=bet_size_list, bets=bets, winning_probability=winning_probability)
df.columns = [f"{int(100*value)}%" for value in bet_size_list]

fig = go.Figure()
for column in df.columns:
    fig.add_trace(go.Scatter(x=df.index, y=df[column], name=column))
fig.update_layout(title='Normalized Cumulative Returns', 
                    xaxis_title='Bets',
                height=600,
                width=950,
                legend=dict(title='Bet Size',
                            orientation="h",
                            yanchor="bottom",
                            y=1.02,
                            xanchor="right",
                            x=1))
fig.show()

In [106]:
# Function to calculate the impact of a win followed by a loss
def calculate_impact(initial_amount, leverage, win, loss):
    edge = win + loss
    edge_impact = round(initial_amount*leverage*edge, 2)
    partial_amount = initial_amount + round(initial_amount*leverage*win, 2)
    final_amount = round(partial_amount*leverage*(loss) + partial_amount, 2)
    drag_impact = final_amount - (initial_amount+edge_impact)
    pnl = round(100*((final_amount/initial_amount) - 1), 2)
    return [edge_impact, drag_impact, final_amount, pnl]

In [107]:
# Define parameters
initial_amount = 100
leverage_list = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
win = 0.1
loss = -0.05
edge_impact_list = []
drag_impact_list = []
final_amount_list = []
pnl_list = []

# Loop through different values of leverage and calculate impacts
for leverage in leverage_list:

    results = calculate_impact(initial_amount, leverage, win, loss)
    edge_impact_list.append(results[0])
    drag_impact_list.append(results[1])
    final_amount_list.append(results[2])
    pnl_list.append(results[3])

final_df = {'Leverage':leverage_list,
            'Edge Impact':edge_impact_list,
            'Drag Impact':drag_impact_list,
            'Final Amount':final_amount_list,
            'PnL':pnl_list}

final_df = pd.DataFrame(final_df)
final_df['Profit'] = final_df['Final Amount'] - initial_amount
final_df

# Plot results
fig = go.Figure()
fig.add_trace(go.Scatter(x=final_df['Leverage'], y=final_df['Edge Impact'], name='Edge Impact'))
fig.add_trace(go.Scatter(x=final_df['Leverage'], y=final_df['Drag Impact'], name='Drag Impact'))
fig.add_trace(go.Scatter(x=final_df['Leverage'], y=final_df['Profit'], name='Profit'))
fig.update_layout(title='Edge Impact x Drag Impact',
                    xaxis_title='Leverage (x Initial Amount)',
                    yaxis_title='$',
                height=600,
                width=950,
                legend=dict(title='Legend',
                            orientation="h",
                            yanchor="bottom",
                            y=1.02,
                            xanchor="right",
                            x=1))
fig.show()

## Monte Carlo simulation of sequence of bets

In [108]:
# Define parameters
initial_amount = 1
bet_size_list = [0.04]
bets = 1000
iterations = 100
winning_probability = 0.52
monte_carlo_df = pd.DataFrame()

# Run Monte Carlo simulation to see distribution of returns
for i in range(iterations):

    outputs, df = cumulative_bets(initial_amount=initial_amount, bet_size_list=bet_size_list, bets=bets, winning_probability=winning_probability)
    monte_carlo_df = pd.concat([monte_carlo_df, df], axis=1)
monte_carlo_df.columns = [f"{value}" for value in range(iterations)]

# Plot results
fig = go.Figure()
for column in monte_carlo_df.columns:
    fig.add_trace(go.Scatter(x=monte_carlo_df.index, y=monte_carlo_df[column], name=column))
fig.update_yaxes(type="log")
fig.update_layout(title='Normalized Cumulative Returns', 
                    xaxis_title='Bets',
                height=600,
                width=950,
                showlegend=False)
fig.show()

In [109]:
# Plot histogram of results
final_return = pd.DataFrame(monte_carlo_df.iloc[-1].transpose())
final_return.columns = ['Return']
fig = px.histogram(final_return,
            x=final_return['Return'],
            nbins=100)
fig.show()

## Backtest Adapted Kelly Criterion in Financial Market 

In [111]:
# Define parameters
tickers = ['^GSPC']
rfr = 0

# Download asset data, calculate mean return, variance and kelly
asset = pd.DataFrame(yf.download(tickers, start='2015-01-01', end='2022-12-31')['Close'])
asset['Daily Return'] = asset.pct_change()
mean_return = asset['Daily Return'].mean()
variance = (asset['Daily Return'].std())**2
kelly = (mean_return - rfr)/variance

print('Mean Return:', round(mean_return, 5))
print('Variance:', round(variance, 5))
print('Risk Free Rate:', rfr)
print('Kelly:', round(kelly, 5))

# Perform buy-and-hold vectorized backtest
asset['Benchmark'] = (1+asset['Daily Return']).cumprod()
asset['Benchmark'].fillna(1, inplace=True)
asset['Full Kelly'] = (1+(kelly*asset['Daily Return'])).cumprod()
asset['Half Kelly'] = (1+(0.5*kelly*asset['Daily Return'])).cumprod()
asset['1.5x Kelly'] = (1+(1.5*kelly*asset['Daily Return'])).cumprod()
asset['2x Kelly'] = (1+(2*kelly*asset['Daily Return'])).cumprod()

# Plot results
fig = go.Figure()
fig.add_trace(go.Scatter(x=asset.index, y=asset['Benchmark'], name='Benchmark'))
fig.add_trace(go.Scatter(x=asset.index, y=asset['Full Kelly'], name='Full Kelly'))
fig.add_trace(go.Scatter(x=asset.index, y=asset['Half Kelly'], name='Half Kelly'))
fig.add_trace(go.Scatter(x=asset.index, y=asset['1.5x Kelly'], name='1.5x Kelly'))
fig.update_layout(title='Kelly Criterion in S&P500 - Backtest',
                    xaxis_title='Date',
                    yaxis_title='Normalized Cumulative Return',
                height=600,
                width=950,
                legend=dict(title='Legend',
                            orientation="h",
                            yanchor="bottom",
                            y=1.02,
                            xanchor="right",
                            x=1))
fig.show()

[*********************100%***********************]  1 of 1 completed
Mean Return: 0.00038
Variance: 0.00014
Risk Free Rate: 0
Kelly: 2.69624


## Walk-Forward Test

In [112]:
# Define Parameters
tickers = ['^GSPC']
rfr = 0
asset = pd.DataFrame(yf.download(tickers, start='2015-01-01', end='2022-12-31')['Close'])
asset['Daily Return'] = asset.pct_change()
year_list = [2016, 2017, 2018, 2019, 2020, 2021, 2022]
kelly_list = []
cap_kelly_list = []
results_df = pd.DataFrame(columns=['Benchmark', 'Full Kelly', 'Half Kelly', '1.5x Kelly'])
partial_amount = [1, 1, 1, 1]

# Loop through years
for year in year_list:

    # Split in and out of sample
    last_year_data = asset[asset.index.year == (year-1)].copy()
    this_year_data = asset[asset.index.year == (year)].copy()

    # Calculate kelly using in-sample data
    mean_return = last_year_data['Daily Return'].mean()
    variance = (last_year_data['Daily Return'].std())**2
    formula_kelly = (mean_return - rfr)/variance
    kelly = np.clip(formula_kelly, 0.5, 3)
    kelly_list.append(formula_kelly)
    cap_kelly_list.append(kelly)

    # Vectorized backtest using out of sample data
    this_year_data['Benchmark'] = partial_amount[0]*(1+this_year_data['Daily Return']).cumprod()
    this_year_data['Full Kelly'] = partial_amount[1]*(1+(kelly*this_year_data['Daily Return'])).cumprod()
    this_year_data['Half Kelly'] = partial_amount[2]*(1+(0.5*kelly*this_year_data['Daily Return'])).cumprod()
    this_year_data['1.5x Kelly'] = partial_amount[3]*(1+(1.5*kelly*this_year_data['Daily Return'])).cumprod()
    results_df = pd.concat([results_df, this_year_data])

    partial_amount = [results_df['Benchmark'].iloc[-1], results_df['Full Kelly'].iloc[-1], results_df['Half Kelly'].iloc[-1], results_df['1.5x Kelly'].iloc[-1]]

# Plot Kelly values
fig = go.Figure()
fig.add_trace(go.Scatter(x=year_list, y=kelly_list, name='Kelly'))
fig.add_trace(go.Scatter(x=year_list, y=cap_kelly_list, name='Limited Kelly'))
fig.update_layout(title='Kelly Criterion in S&P500',
                    xaxis_title='Date',
                    yaxis_title='Kelly Leverage',
                height=600,
                width=950,
                legend=dict(title='Legend',
                            orientation="h",
                            yanchor="bottom",
                            y=1.02,
                            xanchor="right",
                            x=1))
fig.show()

[*********************100%***********************]  1 of 1 completed


In [113]:
# Plot test returns
fig = go.Figure()
fig.add_trace(go.Scatter(x=results_df.index, y=results_df['Benchmark'], name='Benchmark'))
fig.add_trace(go.Scatter(x=results_df.index, y=results_df['Full Kelly'], name='Full Kelly'))
fig.add_trace(go.Scatter(x=results_df.index, y=results_df['Half Kelly'], name='Half Kelly'))
fig.add_trace(go.Scatter(x=results_df.index, y=results_df['1.5x Kelly'], name='1.5x Kelly'))
fig.update_layout(title='Kelly Criterion in S&P500 - Walk-Forward Test',
                    xaxis_title='Date',
                    yaxis_title='Normalized Cumulative Return',
                height=600,
                width=950,
                legend=dict(title='Legend',
                            orientation="h",
                            yanchor="bottom",
                            y=1.02,
                            xanchor="right",
                            x=1))
fig.show()